# Access locations and times of Veery encounters

For this challenge, you will use a database called the [Global
Biodiversity Information Facility (GBIF)](https://www.gbif.org/). GBIF
is compiled from species observation data all over the world, and
includes everything from museum specimens to photos taken by citizen
scientists in their backyards.

<link rel="stylesheet" type="text/css" href="./assets/styles.css"><div class="callout callout-style-default callout-titled callout-task"><div class="callout-header"><div class="callout-icon-container"><i class="callout-icon"></i></div><div class="callout-title-container flex-fill">Try It: Explore GBIF</div></div><div class="callout-body-container callout-body"><p>Before your get started, go to the <a
href="https://www.gbif.org/occurrence/search">GBIF occurrences search
page</a> and explore the data.</p></div></div>

> **Contribute to open data**
>
> You can get your own observations added to GBIF using
> [iNaturalist](https://www.inaturalist.org/)!

### Set up your code to prepare for download

We will be getting data from a source called [GBIF (Global Biodiversity
Information Facility)](https://www.gbif.org/). We need a package called
`pygbif` to access the data, which may not be included in your
environment. Install it by running the cell below:

In [2]:
%%bash
pip install pygbif

<link rel="stylesheet" type="text/css" href="./assets/styles.css"><div class="callout callout-style-default callout-titled callout-task"><div class="callout-header"><div class="callout-icon-container"><i class="callout-icon"></i></div><div class="callout-title-container flex-fill">Try It: Import packages</div></div><div class="callout-body-container callout-body"><p>In the imports cell, we’ve included some packages that you will need.
Add imports for packages that will help you:</p>
<ol type="1">
<li>Work with reproducible file paths</li>
<li>Work with tabular data</li>
</ol></div></div>

In [3]:
import time
import zipfile
from getpass import getpass
from glob import glob
import os
import pathlib
import geopandas as gpd
import pandas as pd
import pygbif.occurrences as occ
import pygbif.species as species

In [4]:
# Create data directory in the home folder
data_dir = os.path.join(
    # Home directory
    pathlib.Path.home(),
    # Earth analytics data directory
    'earth-analytics',
    'data',
    # Project directory
    'osprey_distribution',
)
os.makedirs(data_dir, exist_ok=True)

# Define the directory name for GBIF data
gbif_dir = os.path.join(data_dir, 'osprey_distribution')

:::

### Register and log in to GBIF

You will need a [GBIF account](https://www.gbif.org/) to complete this
challenge. You can use your GitHub account to authenticate with GBIF.
Then, run the following code to save your credentials on your computer.

> **Warning**
>
> Your email address **must** match the email you used to sign up for
> GBIF!

> **Tip**
>
> If you accidentally enter your credentials wrong, you can set
> `reset_credentials=True` instead of `reset_credentials=False`.

In [5]:
reset_credentials = False
# GBIF needs a username, password, and email
credentials = dict(
   GBIF_USER=(input, 'username'),
    GBIF_PWD=(getpass, 'password'),
    GBIF_EMAIL=(input, 'email'),
)
for env_variable, (prompt_func, prompt_text) in credentials.items():
    # Delete credential from environment if requested
    if reset_credentials and (env_variable in os.environ):
        os.environ.pop(env_variable)
    # Ask for credential and save to environment
    if not env_variable in os.environ:
        os.environ[env_variable] = prompt_func(prompt_text)

### Get the species key

> ** Your task**
>
> 1.  Replace the `species_name` with the name of the species you want
>     to look up
> 2.  Run the code to get the species key

In [6]:
# Query species
species_info = species.name_lookup('Pandion haliaetus', rank='SPECIES')

# Get the first result
first_result = species_info['results'][0]

# Get the species key (nubKey)
species_key = first_result['nubKey']

# Check the result
first_result['species'], species_key

('Pandion haliaetus', 2480726)

### Download data from GBIF

::: {.callout-task title=“Submit a request to GBIF”

1.  Replace `csv_file_pattern` with a string that will match **any**
    `.csv` file when used in the `glob` function. HINT: the character
    `*` represents any number of any values except the file separator
    (e.g. `/`)

2.  Add parameters to the GBIF download function, `occ.download()` to
    limit your query to:

    -   observations
    -   from 2023
    -   with spatial coordinates.

3.  Then, run the download. **This can take a few minutes**. :::

In [7]:
# Only download once
gbif_pattern = os.path.join(gbif_dir, '*.csv')
if not glob(gbif_pattern):
    # Only submit one request
    if not 'GBIF_DOWNLOAD_KEY' in os.environ:
        # Submit query to GBIF
        gbif_query = occ.download([
            "speciesKey = 2480726",
            "hasCoordinate = TRUE ",
            "year = 2023 ",
        ])
        os.environ['GBIF_DOWNLOAD_KEY'] = gbif_query[0]

    # Wait for the download to build
    download_key = os.environ['GBIF_DOWNLOAD_KEY']
    wait = occ.download_meta(download_key)['status']
    while not wait=='SUCCEEDED':
        wait = occ.download_meta(download_key)['status']
        time.sleep(5)

    # Download GBIF data
    download_info = occ.download_get(
        os.environ['GBIF_DOWNLOAD_KEY'], 
        path=data_dir)

    # Unzip GBIF data
    with zipfile.ZipFile(download_info['path']) as download_zip:
        download_zip.extractall(path=gbif_dir)

# Find the extracted .csv file path (take the first result)
gbif_path = glob(gbif_pattern)[0]

### Load the GBIF data into Python

<link rel="stylesheet" type="text/css" href="./assets/styles.css"><div class="callout callout-style-default callout-titled callout-task"><div class="callout-header"><div class="callout-icon-container"><i class="callout-icon"></i></div><div class="callout-title-container flex-fill">Try It: Load GBIF data</div></div><div class="callout-body-container callout-body"><ol type="1">
<li>Look at the beginning of the file you downloaded using the code
below. What do you think the <strong>delimiter</strong> is?</li>
<li>Run the following code cell. What happens?</li>
<li>Uncomment and modify the parameters of <code>pd.read_csv()</code>
below until your data loads successfully and you have only the columns
you want.</li>
</ol></div></div>

You can use the following code to look at the beginning of your file:

In [8]:
!head -n 2 $gbif_path 

gbifID	datasetKey	occurrenceID	kingdom	phylum	class	order	family	genus	species	infraspecificEpithet	taxonRank	scientificName	verbatimScientificName	verbatimScientificNameAuthorship	countryCode	locality	stateProvince	occurrenceStatus	individualCount	publishingOrgKey	decimalLatitude	decimalLongitude	coordinateUncertaintyInMeters	coordinatePrecision	elevation	elevationAccuracy	depth	depthAccuracy	eventDate	day	month	year	taxonKey	speciesKey	basisOfRecord	institutionCode	collectionCode	catalogNumber	recordNumber	identifiedBy	dateIdentified	license	rightsHolder	recordedBy	typeStatus	establishmentMeans	lastInterpreted	mediaType	issue
4874194707	52f2051b-c47e-403a-8e32-04b2f2273c20	ESA:AranzadiRings:2023530-03010-3958265-0	Animalia	Chordata	Aves	Accipitriformes	Pandionidae	Pandion	Pandion haliaetus		SPECIES	Pandion haliaetus (Linnaeus, 1758)	Pandion haliaetus (Linnaeus, 1758)	(Linnaeus, 1758)	ES		Mallorca	PRESENT		823818f6-0696-4e29-bc4c-b6f3817535a7	39.58	2.65							2023-05-30	30	5	2023	2480

In [9]:
# Load the GBIF data
gbif_df = pd.read_csv(
    gbif_path, 
    delimiter='\t',
    index_col='gbifID',
    usecols=['gbifID','scientificName','countryCode','stateProvince','decimalLatitude','decimalLongitude', 'month','year']
)
gbif_df.head()

scientificName countryCode stateProvince  \
gbifID                                                                     
4874194707  Pandion haliaetus (Linnaeus, 1758)          ES      Mallorca   
4873924113  Pandion haliaetus (Linnaeus, 1758)          ES      Mallorca   
4873883588  Pandion haliaetus (Linnaeus, 1758)          ES       Menorca   
4873883679  Pandion haliaetus (Linnaeus, 1758)          ES        Huelva   
4874176717  Pandion haliaetus (Linnaeus, 1758)          ES      Gipuzkoa   

            decimalLatitude  decimalLongitude  month  year  
gbifID                                                      
4874194707            39.58              2.65    5.0  2023  
4873924113            39.58              2.65    6.0  2023  
4873883588            39.91              4.11    6.0  2023  
4873883679            37.26             -6.91    6.0  2023  
4874176717            43.28             -2.24   12.0  2023

In [10]:
gbif_gdfos = (
    gpd.GeoDataFrame(
        gbif_df, 
        geometry=gpd.points_from_xy(
            gbif_df.decimalLongitude, 
            gbif_df.decimalLatitude), 
        crs="EPSG:4326")
    # Select the desired columns
     [['month', 'geometry']]
)
gbif_gdfos

month                     geometry
gbifID                                        
4874194707    5.0           POINT (2.65 39.58)
4873924113    6.0           POINT (2.65 39.58)
4873883588    6.0           POINT (4.11 39.91)
4873883679    6.0          POINT (-6.91 37.26)
4874176717   12.0          POINT (-2.24 43.28)
...           ...                          ...
4579730933    7.0   POINT (165.1441 -20.75464)
4579731008    7.0  POINT (165.15772 -20.81797)
4579731070    6.0  POINT (165.15772 -20.81797)
4579769323    7.0  POINT (165.15772 -20.81797)
4579769324    7.0    POINT (165.048 -20.66433)

[876723 rows x 2 columns]

In [11]:
# Set up the ecoregion boundary URL
ecoregions_url = (
    "https://storage.googleapis.com/teow2016/Ecoregions2017.zip")

# Set up a path to save the data on your machine
ecoregions_dir = os.path.join(data_dir, 'wwf_ecoregions')
os.makedirs(ecoregions_dir, exist_ok=True)
ecoregions_path = os.path.join(ecoregions_dir, 'wwf_ecoregions.shp')

# Only download once
if not os.path.exists(ecoregions_path):
    ecoregions_gdf = gpd.read_file(ecoregions_url)
    ecoregions_gdf.to_file(ecoregions_path)

In [12]:
# Open up the ecoregions boundaries
ecoregions_gdf = (gpd.read_file(ecoregions_path)
.rename(columns={
        'ECO_NAME': 'name',
        'SHAPE_AREA': 'area'})
    [['name', 'area', 'geometry']]
)


# Name the index so it will match the other data later on
ecoregions_gdf.index.name = 'ecoregion'

In [13]:
gbif_ecoregion_gdfos = (
    ecoregions_gdf
    # Match the CRS of the GBIF data and the ecoregions
    .to_crs(gbif_gdfos.crs)
    # Find ecoregion for each observation
    .sjoin(
        gbif_gdfos,
        how='inner', 
        predicate='contains')
    # Select the required columns
    [['month', 'name']]
    
)
gbif_ecoregion_gdfos

month                                               name
ecoregion                                                          
2            9.0  Aegean and Western Turkey sclerophyllous and m...
2            3.0  Aegean and Western Turkey sclerophyllous and m...
2            5.0  Aegean and Western Turkey sclerophyllous and m...
2            8.0  Aegean and Western Turkey sclerophyllous and m...
2            9.0  Aegean and Western Turkey sclerophyllous and m...
...          ...                                                ...
845         10.0                        Borneo montane rain forests
845          5.0                        Borneo montane rain forests
845          5.0                        Borneo montane rain forests
845          5.0                        Borneo montane rain forests
845          4.0                        Borneo montane rain forests

[814969 rows x 2 columns]

In [14]:
occurrence_df = (
    gbif_ecoregion_gdfos
    # For each ecoregion, for each month...
    .groupby(['ecoregion', 'month'])
    # ...count the number of occurrences
    .agg(occurrences=('name', 'count'))
)

# Get rid of rare observations (possible misidentification?)
occurrence_df = occurrence_df[occurrence_df.occurrences>1]

# Take the mean by ecoregion
mean_occurrences_by_ecoregion = (
    occurrence_df
    .groupby(['ecoregion'])
    .mean()
)
# Take the mean by month
mean_occurrences_by_month = (
    occurrence_df
    .groupby(['month'])
    .mean()
)

# Normalize by space and time for sampling effort
occurrence_df['norm_occurrences'] = (
    occurrence_df
    /mean_occurrences_by_month
    /mean_occurrences_by_ecoregion
)
occurrence_df

occurrences  norm_occurrences
ecoregion month                               
2         1.0              7          0.002842
          2.0              7          0.003192
          3.0              8          0.002705
          4.0             26          0.003954
          5.0             22          0.003190
...                      ...               ...
842       11.0             5          0.009692
          12.0             3          0.004615
843       2.0              3          0.008701
          12.0             2          0.006154
845       5.0              3          0.002305

[3435 rows x 2 columns]

In [15]:
# Get month names
import calendar

# Libraries for Dynamic mapping
import cartopy.crs as ccrs
import panel as pn
import geoviews as gv
import hvplot.pandas

/opt/conda/lib/python3.11/site-packages/dask/dataframe/__init__.py:42: FutureWarning: 
Dask dataframe query planning is disabled because dask-expr is not installed.

You can install it with `pip install dask[dataframe]` or `conda install dask`.
This will raise in a future version.

  warnings.warn(msg, FutureWarning)


In [16]:
# Simplify the geometry to speed up processing
ecoregions_gdf.geometry = ecoregions_gdf.simplify(
    .1, preserve_topology=False)

# Change the CRS to Mercator for mapping
ecoregions_gdf = ecoregions_gdf.to_crs(ccrs.Mercator())

# Check that the plot runs
ecoregions_gdf.hvplot(geo=True, crs=ccrs.Mercator())

:Polygons   [Longitude,Latitude]

In [17]:
# Join the occurrences with the plotting GeoDataFrame
occurrence_gdf = ecoregions_gdf.join(occurrence_df)

# Get the plot bounds so they don't change with the slider
xmin, ymin, xmax, ymax = occurrence_gdf.total_bounds

# Define the slider widget
slider = pn.widgets.DiscreteSlider(
        options={
            calendar.month_name[month_num]: month_num
            for month_num in range(1,13)
        }
)

In [22]:

occurrence_gdf



name       area  \
ecoregion month                                                                 
2         1.0    Aegean and Western Turkey sclerophyllous and m...  13.844952   
          2.0    Aegean and Western Turkey sclerophyllous and m...  13.844952   
          3.0    Aegean and Western Turkey sclerophyllous and m...  13.844952   
          4.0    Aegean and Western Turkey sclerophyllous and m...  13.844952   
          5.0    Aegean and Western Turkey sclerophyllous and m...  13.844952   
...                                                            ...        ...   
842       11.0                       Sulawesi lowland rain forests   9.422097   
          12.0                       Sulawesi lowland rain forests   9.422097   
843       2.0                         East African montane forests   5.010930   
          12.0                        East African montane forests   5.010930   
845       5.0                          Borneo montane rain forests   9.358407   

                                                          geometry  \
ecoregion month                                                      
2         1.0    MULTIPOLYGON (((3391149.749 4336064.109, 33846...   
          2.0    MULTIPOLYGON (((3391149.749 4336064.109, 33846...   
          3.0    MULTIPOLYGON (((3391149.749 4336064.109, 33846...   
          4.0    MULTIPOLYGON (((3391149.749 4336064.109, 33846...   
          5.0    MULTIPOLYGON (((3391149.749 4336064.109, 33846...   
...                                                            ...   
842       11.0   MULTIPOLYGON (((14113374.546 501721.962, 14128...   
          12.0   MULTIPOLYGON (((14113374.546 501721.962, 14128...   
843       2.0    MULTIPOLYGON (((4298787.669 -137583.786, 42727...   
          12.0   MULTIPOLYGON (((4298787.669 -137583.786, 42727...   
845       5.0    MULTIPOLYGON (((13126956.393 539092.917, 13136...   

                 occurrences  norm_occurrences  
ecoregion month                                 
2         1.0              7          0.002842  
          2.0              7          0.003192  
          3.0              8          0.002705  
          4.0             26          0.003954  
          5.0             22          0.003190  
...                      ...               ...  
842       11.0             5          0.009692  
          12.0             3          0.004615  
843       2.0              3          0.008701  
          12.0             2          0.006154  
845       5.0              3          0.002305  

[3435 rows x 5 columns]

In [25]:
# Plot occurrence by ecoregion and month
osprey_migration_plot = (
    occurrence_gdf
    .hvplot(
        c='norm_occurrences',
        groupby='month',
        # Use background tiles
        #geo=True, crs=ccrs.Mercator(), tiles='CartoLight',
        title="Osprey migration",
        frame_height=600,
        frame_width=800,
        colorbar=False,
        widgets={'month': slider},
        widget_location='bottom'
    )
)

In [70]:
occurrence_gdf.hvplot(
     c='norm_occurrences',
     groupby='month',
     geo=True
)

:DynamicMap   [month]
   :Polygons   [Longitude,Latitude]   (norm_occurrences)

In [26]:
osprey_migration_plot

BokehModel(combine_events=True, render_bundle={'docs_json': {'25ffd449-16dd-4e21-8aa6-63f6e2957d20': {'version…

In [27]:
# Save the plot
osprey_migration_plot.save('osprey_migration.html', embed=True)


: 